# Google Review Preprocessing version1 

## version0에서 발견된 문제점 
1. 맞춤법이 틀린 문장은 추후 토크나이징할 때 영향있을거 같음.
2. (Google 번역)처럼 괄호로 둘러쌓인 단어들이 '번역', '원문'과 같은 단어로 남아있음.
3. 코드 정리 필요
4. 전체 데이터셋에 대한 정제 데이터셋 만들어야함.

## Data path 확인

In [1]:
!pwd # 현재 경로 확인 

/home/aiffel-dj19/jungcheck/DataPreprocessing


아래 tree 명령어로 상위 폴더(jungcheck)내 파일 구성을 볼 수 있습니다.    

In [2]:
!ls . # 현재 위치의 file list

data				   googleReviewPreprocessingV1.ipynb  reference
filtered			   naverReviewPreprocessingV0.ipynb
googleReviewPreprocessingV0.ipynb  naverReviewPreprocessingV1.ipynb


In [3]:
!tree -L 3 -N ./data/google_review # jungcheck 폴더내 경로 확인 

./data/google_review
├── 01오월드
│   └── 오월드.csv
├── 02뿌리공원
│   └── 뿌리공원.csv
├── 03엑스포
│   ├── 한빛탑.csv
│   ├── 엑스포다리.csv
│   ├── 엑스포음악분수.csv
│   ├── 엑스포과학공원.csv
│   └── 세계엑스포기념품박물관.csv
├── 04한밭수목원
│   └── 한밭수목원.csv
├── 05계족산
│   ├── 계족산(봉우리읍내동).csv
│   ├── 계족산성.csv
│   └── 계족산황톳길.csv
├── 06대청호
│   ├── 대청호.csv
│   ├── 대청댐물문화관.csv
│   └── 대청호반자연생태공원.csv
├── 07장태산
│   ├── 장태산자연휴양림.csv
│   ├── 장태산자연휴양림전망대.csv
│   ├── 장태산자연휴양림숲속의집.csv
│   └── 장태산자연휴양림메타세콰이어산림욕장.csv
├── 09동춘당
│   ├── 회덕동춘당.csv
│   └── 동춘당공원.csv
├── 11으능정이문화의거리
│   ├── 으능정이거리.csv
│   ├── 대전스카이로드.csv
│   └── 으능정이문화거리.csv
├── 12유성온천
│   ├── 유성온천공원.csv
│   └── 유성온천족욕체험장.csv
├── 13성심당
│   ├── 성심당본점.csv
│   ├── 성심당대전역점.csv
│   ├── 성심당케잌부띠끄본점.csv
│   ├── 성심당롯데백화점대전점.csv
│   └── 성심당DCC점.csv
├── 13시민천문대
│   └── 대전시민천문대.csv
├── 14수통골
│   ├── 수통골유원지.csv
│   └── 계룡산국립공원수통골지구.csv
├── 16대전문화예술단지
│   ├── 이응노미술관.csv
│   ├── 대전예술의전당.csv
│   └── 대전시립미술관.csv
└── 17국립중앙과학관
    └── 국립중앙과학관.csv

15 directories, 37 files


## Library Import

In [43]:
import os 
import glob
from tqdm import tqdm

import re
import pandas as pd 
import copy # deep copy

from hanspell import spell_checker # 한글 맞춤법 검사기 
from hangul_checker import KoreanSpellChecker # 한글 맞춤법 검사기 
from pykospacing import Spacing # 한글 띄어쓰기 검사기 

## Data Load 

In [5]:
data_path = os.path.join(os.getcwd(), 'data/google_review/')
data_path

'/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/'

In [7]:
folders = os.listdir(data_path)
print(folders)
print(len(folders)) # 17개 대상 관광지 중 15개 

['07장태산', '05계족산', '09동춘당', '11으능정이문화의거리', '02뿌리공원', '03엑스포', '13성심당', '14수통골', '12유성온천', '04한밭수목원', '17국립중앙과학관', '06대청호', '16대전문화예술단지', '13시민천문대', '01오월드']
15


👉 17개 대상 관광지 중에 15개 데이터만 크롤링 해올 수 있었습니다. 구글 리뷰 같은 경우 한밭야구장과 둘레길은 리뷰가 없거나 2개 이하 였기 때문에 데이터셋에 포함되지 않습니다.    
👉 감성 분석 결과를 네이버 블로그 리뷰와 합쳐서 17개 대상 관광지들에 대한 감성 분석을 진행합니다.
👉 카이스트 같은 경우 크롤링 데이터셋에 있었지만, 대상 관광지에 포함되지 않아 코드 진행하기 전에 디렉토리에서 삭제했습니다.

In [10]:
# 대전관광 홈페이지 영문버전을 참고했으며(단, 긴 경우 줄임), 해당 리스트는 정제후 파일명으로 사용
# 나오지 않는 관광지는 네이버 검색 기준을 따름
keywords_ko = [file_name[2:] for file_name in folders]
keywords_en = ['jangtae_mountain', 'gyejok_mountain', 'dongchundang', 'uineungjeongi_street', 'ppuri_park', 
               'expo_science_park', 'sungsimdang_bakery', 'water_barrel', 'yuseong_hotspring', 'hanbat_arboretum', 
               'science_museum','daecheong_lake', 'art_culture_complex', 'observatory', 'oworld_zoo']

keywords = {k:v for k, v in zip(keywords_ko, keywords_en)}
keywords

{'장태산': 'jangtae_mountain',
 '계족산': 'gyejok_mountain',
 '동춘당': 'dongchundang',
 '으능정이문화의거리': 'uineungjeongi_street',
 '뿌리공원': 'ppuri_park',
 '엑스포': 'expo_science_park',
 '성심당': 'sungsimdang_bakery',
 '수통골': 'water_barrel',
 '유성온천': 'yuseong_hotspring',
 '한밭수목원': 'hanbat_arboretum',
 '국립중앙과학관': 'science_museum',
 '대청호': 'daecheong_lake',
 '대전문화예술단지': 'art_culture_complex',
 '시민천문대': 'observatory',
 '오월드': 'oworld_zoo'}

👉 대전관광 홈페이지 영문버전을 참고했습니다. (단, 긴 경우 줄임)    
👉 맨 뒤에 단어는 해당 관광지가 어떤 유형의 장소에 해당하는지를 나타내는 단어로 통일성을 줬습니다. 감성 분석을 할 때 성능이 잘 안 나오다면, 장소 유형이 같은 대상끼리 단어사전을 만들어주는 방법도 생각해볼 수 있습니다. 

In [30]:
# root_path내의 dataframe을 합해주는 함수
def concatCsv(root_path, folders_list):
    data_list = []
    
    for folder in folders_list:
        folder_path = os.path.join(root_path, folder)
        
        for file in os.listdir(folder_path):
            file_path = os.path.join(folder_path, file)
            print(file_path)
            
            search = file.split('.')[0]               # 파일명에서 키워드만 추출    
            df = pd.read_csv(file_path, encoding='utf-8')  # csv 파일 읽기
            df['search'] = search
            
            for _,value in keywords.items():
                df['keyword'] = value
            data_list.append(df)
        print('-'*20)
    df = pd.concat(data_list, axis=0)

    return df

In [34]:
data_df = concatCsv(data_path, folders)

/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/07장태산/장태산자연휴양림메타세콰이어산림욕장.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/07장태산/장태산자연휴양림.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/07장태산/장태산자연휴양림전망대.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/07장태산/장태산자연휴양림숲속의집.csv
--------------------
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/05계족산/계족산황톳길.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/05계족산/계족산(봉우리읍내동).csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/05계족산/계족산성.csv
--------------------
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/09동춘당/회덕동춘당.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/09동춘당/동춘당공원.csv
--------------------
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/11으능정이문화의거리/으능정이거리.csv
/home/aiffel-dj19/jungcheck/DataPreprocessing/data/google_review/11으능정이문화의거리/대전스카이로드.

In [35]:
data_df

name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
4             JY Jeong         4  8달 전   
..                  ...      ...   ...   
925                김경영         4  1년 전   
926               패티가고         5  1년 전   
927                이종진         3  1년 전   
928                김소연         5  1년 전   
929            별사탕이랑햄찌         3  1년 전   

                                               comment              search  \
0                    여기는 갈 때마다 새로운 느낌이야 즐거운 시간이 되었습니다.  장태산자연휴양림메타세콰이어산림욕장   
1                                하늘보고 누워 힐링하기 넘 좋은곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘 정리된 메타세쿼이아 숲에서 산림욕 하기 좋은 곳으로 둘레길 걷기와 전망대까지 가...  장태산자연휴양림메타세콰이어산림욕장   
3                                       산책 하기 너무 좋은 명소  장태산자연휴양림메타세콰이어산림욕장   
4                                                   없음  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
925                                               괜찮아요                 오월드   
926                                                 없음                 오월드   
927                                                 없음                 오월드   
928                                     겨울에도 놀기 좋아요~ㅎㅎ                 오월드   
929                                                 없음                 오월드   

        keyword  
0    oworld_zoo  
1    oworld_zoo  
2    oworld_zoo  
3    oworld_zoo  
4    oworld_zoo  
..          ...  
925  oworld_zoo  
926  oworld_zoo  
927  oworld_zoo  
928  oworld_zoo  
929  oworld_zoo  

[18800 rows x 6 columns]

In [32]:
type(data_df['keyword'].iloc[0])

str

In [33]:
# keyword 누락된 열 없는지 확인
data_df['keyword'].isnull().sum()

0

## Data cleaning
* null 처리 
* 일정 길이 이하의 문자열 제거 
* 중복 제거 

In [36]:
# null 처리
print(f'Before length: {len(data_df)}')

data_df = data_df[data_df['comment'] != '없음']
print(f'After length: {len(data_df)}')

Before length: 18800
After length: 8635


In [37]:
# 단어 1개인 경우 확인 
data_df[data_df['comment'].map(len) == 1]

name  ratings   date comment        search     keyword
63             채규삼         5   3주 전       ㆍ      장태산자연휴양림  oworld_zoo
521           남홍계용         5   7달 전       😀      장태산자연휴양림  oworld_zoo
732    hunyong lee         5   9달 전       츠      장태산자연휴양림  oworld_zoo
929            전영옥         4   1년 전       ᆞ      장태산자연휴양림  oworld_zoo
20    남LeeSoonChul         4   3달 전       😀          계족산성  oworld_zoo
84             허현강         5   9달 전       굿          계족산성  oworld_zoo
526            김상민         5   2년 전       굿          계족산성  oworld_zoo
72             물방울         5   2달 전       굳       대전스카이로드  oworld_zoo
270         대전아트카튠         5   8달 전       굿       대전스카이로드  oworld_zoo
278            양성혁         4   9달 전       큼       대전스카이로드  oworld_zoo
489            문주현         3   1년 전       굿       대전스카이로드  oworld_zoo
869            조원화         5   1년 전       굿       대전스카이로드  oworld_zoo
17             항아리         5   2주 전       굳          뿌리공원  oworld_zoo
114           99마루         5   2달 전       굳          뿌리공원  oworld_zoo
283            최일훈         5   6달 전       😃          뿌리공원  oworld_zoo
324            박수민         5   6달 전       ㅁ          뿌리공원  oworld_zoo
504            이영화         5  11달 전       네          뿌리공원  oworld_zoo
5              전유진         5   2일 전       굿         엑스포다리  oworld_zoo
190            김준선         5   6달 전       굿         엑스포다리  oworld_zoo
8              노태훈         4   2일 전       굿           한빛탑  oworld_zoo
58            잘난서방         4   2주 전       굿       성심당DCC점  oworld_zoo
365            최일훈         5   4달 전       굿       성심당DCC점  oworld_zoo
513     Jihong Min         5   6달 전       💜       성심당DCC점  oworld_zoo
543             오현         5   6달 전       빵       성심당DCC점  oworld_zoo
15    Jong Suk Woo         4   2일 전       ㅇ         성심당본점  oworld_zoo
79             김한별         5   2주 전       굿         성심당본점  oworld_zoo
493            정원오         5   3달 전       ㅇ         성심당본점  oworld_zoo
576          냥아치TV         5   3달 전       굳         성심당본점  oworld_zoo
726            오세훈         5   5달 전       굿         성심당본점  oworld_zoo
16             한석화         5   2주 전       굿   성심당롯데백화점대전점  oworld_zoo
433            노희찬         4  10달 전       굳   성심당롯데백화점대전점  oworld_zoo
502             자옹         3   8달 전       굳  계룡산국립공원수통골지구  oworld_zoo
14             장윤주         5   1달 전       굿     유성온천족욕체험장  oworld_zoo
100            이종민         5   1달 전       굿         한밭수목원  oworld_zoo
210     jongku LEE         5   2달 전       굿         한밭수목원  oworld_zoo
554           한 상영         5   8달 전       ㅕ         한밭수목원  oworld_zoo
384            황혜미         5   1년 전       굿       국립중앙과학관  oworld_zoo
11             지성구         4   2주 전       굿       대전예술의전당  oworld_zoo
290            신지완         5   1년 전       굳       대전예술의전당  oworld_zoo
314            정종길         5   1년 전       굿       대전예술의전당  oworld_zoo
320           스텔라김         5   1년 전       짱       대전예술의전당  oworld_zoo
110            쭉쟁이         5   1년 전       굿       대전시립미술관  oworld_zoo
47             강적봉         5   8년 전       짱       대전시민천문대  oworld_zoo
68            잘난서방         4   2주 전       굿           오월드  oworld_zoo
101            배근효         5   3주 전       굿           오월드  oworld_zoo
178            이예빈         5   1달 전       👌           오월드  oworld_zoo
308            신은미         4   3달 전       뿡           오월드  oworld_zoo
403            오진우         5   5달 전       잼           오월드  oworld_zoo
428            류라히         5   6달 전       굿           오월드  oworld_zoo
633    daniel. ggl         4   8달 전       굿           오월드  oworld_zoo

데이터를 확인했을때 유의미한 경우에 모두 해당했기 때문에 length=1인 데이터 유지 

In [38]:
# 단어 0개인 comment 제외 
print(f'Before length: {len(data_df)}')

data_df = data_df[data_df['comment'].map(len) > 0] 
print(f'After length: {len(data_df)}')

Before length: 8635
After length: 8635


In [39]:
# 중복제거 
print(f'Before length: {len(data_df)}')

data_df = data_df.drop_duplicates(['name', 'keyword', 'date']) # name과 keyword, date 모두 중복일때 제거 
print(f'After length: {len(data_df)}')

Before length: 8635
After length: 7875


In [40]:
data_df

name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
6                  박은선         5  1년 전   
..                  ...      ...   ...   
921      young wu Kwon         5  1년 전   
922              강강수월래         4  1년 전   
924                원언니         5  1년 전   
925                김경영         4  1년 전   
928                김소연         5  1년 전   

                                               comment              search  \
0                    여기는 갈 때마다 새로운 느낌이야 즐거운 시간이 되었습니다.  장태산자연휴양림메타세콰이어산림욕장   
1                                하늘보고 누워 힐링하기 넘 좋은곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘 정리된 메타세쿼이아 숲에서 산림욕 하기 좋은 곳으로 둘레길 걷기와 전망대까지 가...  장태산자연휴양림메타세콰이어산림욕장   
3                                       산책 하기 너무 좋은 명소  장태산자연휴양림메타세콰이어산림욕장   
6                          주말마자 애정하는 장태산나들이:-) 단풍도 예뻐요  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
921                                           재밌어요..😍😍                 오월드   
922                                       애들놀고 구경거리는 굿                 오월드   
924                             초등생전용놀이공원으로  아담하고  이뻐요                 오월드   
925                                               괜찮아요                 오월드   
928                                     겨울에도 놀기 좋아요~ㅎㅎ                 오월드   

        keyword  
0    oworld_zoo  
1    oworld_zoo  
2    oworld_zoo  
3    oworld_zoo  
6    oworld_zoo  
..          ...  
921  oworld_zoo  
922  oworld_zoo  
924  oworld_zoo  
925  oworld_zoo  
928  oworld_zoo  

[7875 rows x 6 columns]

## Data preprocessing

In [41]:
filtered_df = copy.deepcopy(data_df)

데이터셋을 살펴보면, 외국인이 작성한 것도 한글로 번역되어 크롤링됐다.
따로 영어를 살려줄 필요 없어 보이므로 한글, ~숫자~ 제외하고 다 제거한다. 

In [45]:
# 번역, 원문과 같이 구글 번역에 의해 나타나는 단어를 제거하는 정규표현식 패턴
test = '안녕하 (번역 제공) 번역 원문 안녕하'
re.sub("[번역 제공|번역|원문]", "", test)
re.sub("[(].*?[)]", "", test)

'안녕하  번역 원문 안녕하'

In [46]:
# filtered_df['comment'] = filtered_df['comment'].str.replace("[^ㄱ-ㅎㅏ-ㅣ가-힣 ]","")
filtered_df['comment'] = filtered_df['comment'].str.replace("[(].*?[)]","", regex=True) # 괄호 사이 단어 제거
filtered_df['comment'] = filtered_df['comment'].str.replace("[번역 제공|번역|원문]","", regex=True) # 위에 정규표현식 적용안되서 다시 적용
filtered_df['comment'] = filtered_df['comment'].str.replace("[^가-힣]","", regex=True) # 완성형 한글만
filtered_df

name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
6                  박은선         5  1년 전   
..                  ...      ...   ...   
921      young wu Kwon         5  1년 전   
922              강강수월래         4  1년 전   
924                원언니         5  1년 전   
925                김경영         4  1년 전   
928                김소연         5  1년 전   

                                               comment              search  \
0                            여기는갈때마다새로운느낌이야즐거운시간이되었습니다  장태산자연휴양림메타세콰이어산림욕장   
1                                    하늘보고누워힐링하기넘좋은곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘정리된메타세쿼이아숲에서산림욕하기좋은곳으로둘레길걷기와전망대까지가벼운등산활동까지할수있...  장태산자연휴양림메타세콰이어산림욕장   
3                                           산책하기너무좋은명소  장태산자연휴양림메타세콰이어산림욕장   
6                                 주말마자애정하는장태산나들이단풍도예뻐요  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
921                                               재밌어요                 오월드   
922                                         애들놀고구경거리는굿                 오월드   
924                                   초등생전용놀이으로아담하고이뻐요                 오월드   
925                                               괜찮아요                 오월드   
928                                          겨울에도놀기좋아요                 오월드   

        keyword  
0    oworld_zoo  
1    oworld_zoo  
2    oworld_zoo  
3    oworld_zoo  
6    oworld_zoo  
..          ...  
921  oworld_zoo  
922  oworld_zoo  
924  oworld_zoo  
925  oworld_zoo  
928  oworld_zoo  

[7875 rows x 6 columns]

👉 정규표현식을 통해 제거 후에, 문장 구성이 달라지기 때문에 cleaning 작업을 위와 똑같이 다시 진행해줍니다.

In [47]:
# 단어 1개인 경우 확인 
filtered_df[filtered_df['comment'].map(len) == 1]

name  ratings   date comment        search     keyword
695    Soo Young Yoo         5   8달 전       굿      장태산자연휴양림  oworld_zoo
732      hunyong lee         5   9달 전       츠      장태산자연휴양림  oworld_zoo
84               허현강         5   9달 전       굿          계족산성  oworld_zoo
324    Soo Young Yoo         5   1년 전       굿          계족산성  oworld_zoo
526              김상민         5   2년 전       굿          계족산성  oworld_zoo
40               김기백         5   2년 전       굿         회덕동춘당  oworld_zoo
72               물방울         5   2달 전       굳       대전스카이로드  oworld_zoo
270           대전아트카튠         5   8달 전       굿       대전스카이로드  oworld_zoo
278              양성혁         4   9달 전       큼       대전스카이로드  oworld_zoo
489              문주현         3   1년 전       굿       대전스카이로드  oworld_zoo
869              조원화         5   1년 전       굿       대전스카이로드  oworld_zoo
908           지존팬지엔k         1   1년 전       앙       대전스카이로드  oworld_zoo
8               韓國青年         5   1주 전       굿          뿌리공원  oworld_zoo
17               항아리         5   2주 전       굳          뿌리공원  oworld_zoo
114             99마루         5   2달 전       굳          뿌리공원  oworld_zoo
504              이영화         5  11달 전       네          뿌리공원  oworld_zoo
5                전유진         5   2일 전       굿         엑스포다리  oworld_zoo
190              김준선         5   6달 전       굿         엑스포다리  oworld_zoo
204           욧이나묵어라         4   6달 전       굿         엑스포다리  oworld_zoo
270              김칠성         5   8달 전       음         엑스포다리  oworld_zoo
8                노태훈         4   2일 전       굿           한빛탑  oworld_zoo
560        mini star         4   1년 전       굿           한빛탑  oworld_zoo
58              잘난서방         4   2주 전       굿       성심당DCC점  oworld_zoo
79               조재현         5   3주 전       짱       성심당DCC점  oworld_zoo
365              최일훈         5   4달 전       굿       성심당DCC점  oworld_zoo
543               오현         5   6달 전       빵       성심당DCC점  oworld_zoo
708     CHANGSOO KIM         5   9달 전       굿       성심당DCC점  oworld_zoo
27               이원희         5   3일 전       굿         성심당본점  oworld_zoo
79               김한별         5   2주 전       굿         성심당본점  oworld_zoo
576            냥아치TV         5   3달 전       굳         성심당본점  oworld_zoo
726              오세훈         5   5달 전       굿         성심당본점  oworld_zoo
883           아하후아하후         5   6달 전       쉬         성심당본점  oworld_zoo
16               한석화         5   2주 전       굿   성심당롯데백화점대전점  oworld_zoo
320              박은영         5   6달 전       굿   성심당롯데백화점대전점  oworld_zoo
433              노희찬         4  10달 전       굳   성심당롯데백화점대전점  oworld_zoo
713              김광용         5   2년 전       굳   성심당롯데백화점대전점  oworld_zoo
502               자옹         3   8달 전       굳  계룡산국립공원수통골지구  oworld_zoo
880   young jun kwon         5   1년 전       굿  계룡산국립공원수통골지구  oworld_zoo
221     Seungmin Lim         5   1년 전       굿        수통골유원지  oworld_zoo
66     Diomar Corpuz         5   4년 전       큰        유성온천공원  oworld_zoo
14               장윤주         5   1달 전       굿     유성온천족욕체험장  oworld_zoo
100              이종민         5   1달 전       굿         한밭수목원  oworld_zoo
210       jongku LEE         5   2달 전       굿         한밭수목원  oworld_zoo
900          young C         5   1년 전       큰         한밭수목원  oworld_zoo
384              황혜미         5   1년 전       굿       국립중앙과학관  oworld_zoo
665    jae hong ryoo         5   1년 전       굿       국립중앙과학관  oworld_zoo
726        Raphael P         5   1년 전       룡       국립중앙과학관  oworld_zoo
487           샤방샤방39         5   3년 전       굿       대청댐물문화관  oworld_zoo
11               지성구         4   2주 전       굿       대전예술의전당  oworld_zoo
320             스텔라김         5   1년 전       짱       대전예술의전당  oworld_zoo
694              박형숙         5   2년 전       굿       대전예술의전당  oworld_zoo
110              쭉쟁이         5   1년 전       굿       대전시립미술관  oworld_zoo
47               강적봉         5   8년 전       짱       대전시민천문대  oworld_zoo
101              배근효         5   3주 전       굿           오월드  oworld_zoo
308              신은미         4   3달 전       뿡           오

👉 데이터를 확인했을때 유의미한 경우에 모두 해당했기 때문에 length=1인 데이터 유지했습니다. 

In [48]:
# 단어 0개인 comment 제외 
print(f'Before length: {len(filtered_df)}')

filtered_df = filtered_df[filtered_df['comment'].map(len) > 0] 
print(f'After length: {len(filtered_df)}')

Before length: 7875
After length: 7837


In [49]:
# 중복제거 
print(f'Before length: {len(filtered_df)}')

filtered_df = filtered_df.drop_duplicates(['name', 'keyword', 'date']) # name과 keyword, date 모두 중복일때 제거 
print(f'After length: {len(filtered_df)}')

Before length: 7837
After length: 7837


In [50]:
filtered_df

name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
6                  박은선         5  1년 전   
..                  ...      ...   ...   
921      young wu Kwon         5  1년 전   
922              강강수월래         4  1년 전   
924                원언니         5  1년 전   
925                김경영         4  1년 전   
928                김소연         5  1년 전   

                                               comment              search  \
0                            여기는갈때마다새로운느낌이야즐거운시간이되었습니다  장태산자연휴양림메타세콰이어산림욕장   
1                                    하늘보고누워힐링하기넘좋은곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘정리된메타세쿼이아숲에서산림욕하기좋은곳으로둘레길걷기와전망대까지가벼운등산활동까지할수있...  장태산자연휴양림메타세콰이어산림욕장   
3                                           산책하기너무좋은명소  장태산자연휴양림메타세콰이어산림욕장   
6                                 주말마자애정하는장태산나들이단풍도예뻐요  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
921                                               재밌어요                 오월드   
922                                         애들놀고구경거리는굿                 오월드   
924                                   초등생전용놀이으로아담하고이뻐요                 오월드   
925                                               괜찮아요                 오월드   
928                                          겨울에도놀기좋아요                 오월드   

        keyword  
0    oworld_zoo  
1    oworld_zoo  
2    oworld_zoo  
3    oworld_zoo  
6    oworld_zoo  
..          ...  
921  oworld_zoo  
922  oworld_zoo  
924  oworld_zoo  
925  oworld_zoo  
928  oworld_zoo  

[7837 rows x 6 columns]

In [51]:
def spacingCorrect(sen):
    spacing = Spacing(rules=keywords_ko+['이뻐요'])
#     print(f'Before sentence: {sen}')

    sen = spacing(sen)
#     print(f'After sentence: {sen}')
#     print('-'*40)
    
    return sen

In [60]:
def spellCorrect(sen):
#     ksc = KoreanSpellChecker()
#     print(f'Before sentence: {sen}')

#     sen = ksc.check_spelling(sen)
#     print(f'After sentence: {sen}')
#     print('-'*40)
    result = spell_checker.check(sen)
    sen = result.as_dict()['checked']
    return sen

### 오래 걸림

In [53]:
# 4분 34초 소요
filtered_df['comment'] = [spacingCorrect(sen) for sen in tqdm(filtered_df['comment'])]
filtered_df

100%|██████████| 7837/7837 [04:28<00:00, 29.16it/s]


name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
6                  박은선         5  1년 전   
..                  ...      ...   ...   
921      young wu Kwon         5  1년 전   
922              강강수월래         4  1년 전   
924                원언니         5  1년 전   
925                김경영         4  1년 전   
928                김소연         5  1년 전   

                                               comment              search  \
0                    여기는 갈 때마다 새로운 느낌이 야 즐거운 시간이 되었습니다  장태산자연휴양림메타세콰이어산림욕장   
1                              하늘 보고 누워 힐링하기 넘 좋은 곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘 정리된 메타세쿼이아숲에서 산림욕하기 좋은 곳으로 둘레길 걷기와 전망대까지 가벼운...  장태산자연휴양림메타세콰이어산림욕장   
3                                        산책하기 너무 좋은 명소  장태산자연휴양림메타세콰이어산림욕장   
6                            주말 마자애정하는 장태산 나들이 단풍도 예뻐요  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
921                                               재밌어요                 오월드   
922                                      애들 놀고 구경거리는 굿                 오월드   
924                               초등생 전용 놀이으로 아담하고 이뻐요                 오월드   
925                                               괜찮아요                 오월드   
928                                        겨울에도 놀기 좋아요                 오월드   

        keyword  
0    oworld_zoo  
1    oworld_zoo  
2    oworld_zoo  
3    oworld_zoo  
6    oworld_zoo  
..          ...  
921  oworld_zoo  
922  oworld_zoo  
924  oworld_zoo  
925  oworld_zoo  
928  oworld_zoo  

[7837 rows x 6 columns]

In [74]:
# # KoreanSpellChecker를 사용할 경우, 맞춤법 검사기의 최대 허용 글자수는 500자이므로, 글자수 제한을 둬야함.
# print(f'Before length: {len(filtered_df)}')

# filtered_df = filtered_df[filtered_df['comment'].map(len) <= 500] # name과 keyword, date 모두 중복일때 제거 
# print(f'After length: {len(filtered_df)}')

In [61]:
# 7분 4초 정도 소요
filtered_df['comment'] = [spellCorrect(sen) for sen in tqdm(filtered_df['comment'])]
filtered_df




  0%|          | 0/7837 [00:00<?, ?it/s]


  0%|          | 2/7837 [00:00<07:35, 17.21it/s]


  0%|          | 4/7837 [00:00<08:17, 15.74it/s]


  0%|          | 7/7837 [00:00<12:08, 10.75it/s]


  0%|          | 11/7837 [00:00<10:00, 13.04it/s]


  0%|          | 13/7837 [00:01<12:02, 10.83it/s]


  0%|          | 16/7837 [00:01<09:36, 13.57it/s]


  0%|          | 21/7837 [00:01<06:44, 19.32it/s]


  0%|          | 24/7837 [00:01<06:26, 20.20it/s]


  0%|          | 27/7837 [00:01<06:19, 20.57it/s]


  0%|          | 32/7837 [00:01<05:04, 25.67it/s]


  0%|          | 36/7837 [00:01<04:30, 28.88it/s]


  1%|          | 40/7837 [00:02<04:44, 27.40it/s]


  1%|          | 43/7837 [00:02<06:25, 20.24it/s]


  1%|          | 47/7837 [00:02<05:41, 22.81it/s]


  1%|          | 50/7837 [00:02<06:03, 21.41it/s]


  1%|          | 54/7837 [00:02<05:14, 24.74it/s]


  1%|          | 57/7837 [00:02<05:04, 25.57it/s]


  1%|          | 60/7837 [00:02<05:56, 21.83it/s]


  1%|          | 63/7

  6%|▌         | 466/7837 [00:22<04:17, 28.57it/s]


  6%|▌         | 471/7837 [00:22<03:49, 32.10it/s]


  6%|▌         | 475/7837 [00:22<03:56, 31.16it/s]


  6%|▌         | 479/7837 [00:23<04:07, 29.74it/s]


  6%|▌         | 483/7837 [00:23<04:14, 28.87it/s]


  6%|▌         | 486/7837 [00:23<04:59, 24.57it/s]


  6%|▌         | 489/7837 [00:23<04:55, 24.86it/s]


  6%|▋         | 494/7837 [00:23<04:09, 29.43it/s]


  6%|▋         | 498/7837 [00:23<05:29, 22.30it/s]


  6%|▋         | 502/7837 [00:24<04:59, 24.48it/s]


  6%|▋         | 506/7837 [00:24<04:57, 24.64it/s]


  6%|▋         | 509/7837 [00:24<05:24, 22.58it/s]


  7%|▋         | 513/7837 [00:24<04:40, 26.12it/s]


  7%|▋         | 518/7837 [00:24<04:03, 30.05it/s]


  7%|▋         | 522/7837 [00:24<03:47, 32.21it/s]


  7%|▋         | 526/7837 [00:24<04:09, 29.36it/s]


  7%|▋         | 530/7837 [00:25<04:14, 28.71it/s]


  7%|▋         | 534/7837 [00:25<05:08, 23.66it/s]


  7%|▋         | 537/7837 [00:25<05:03, 24.03i

 12%|█▏        | 964/7837 [00:43<05:51, 19.55it/s]


 12%|█▏        | 970/7837 [00:43<04:26, 25.79it/s]


 12%|█▏        | 974/7837 [00:43<04:07, 27.68it/s]


 12%|█▏        | 978/7837 [00:44<03:52, 29.50it/s]


 13%|█▎        | 982/7837 [00:44<04:56, 23.14it/s]


 13%|█▎        | 986/7837 [00:44<04:20, 26.26it/s]


 13%|█▎        | 991/7837 [00:44<03:57, 28.78it/s]


 13%|█▎        | 995/7837 [00:44<04:45, 23.93it/s]


 13%|█▎        | 999/7837 [00:44<04:18, 26.49it/s]


 13%|█▎        | 1003/7837 [00:45<04:54, 23.23it/s]


 13%|█▎        | 1006/7837 [00:45<04:41, 24.24it/s]


 13%|█▎        | 1009/7837 [00:45<06:08, 18.51it/s]


 13%|█▎        | 1012/7837 [00:45<06:55, 16.44it/s]


 13%|█▎        | 1015/7837 [00:45<06:05, 18.69it/s]


 13%|█▎        | 1021/7837 [00:46<04:21, 26.08it/s]


 13%|█▎        | 1025/7837 [00:46<05:19, 21.30it/s]


 13%|█▎        | 1028/7837 [00:46<04:57, 22.88it/s]


 13%|█▎        | 1031/7837 [00:46<04:50, 23.47it/s]


 13%|█▎        | 1035/7837 [00:46<04:

 19%|█▉        | 1521/7837 [01:05<04:25, 23.82it/s]


 19%|█▉        | 1525/7837 [01:05<04:46, 22.03it/s]


 20%|█▉        | 1530/7837 [01:05<04:18, 24.43it/s]


 20%|█▉        | 1534/7837 [01:05<04:11, 25.03it/s]


 20%|█▉        | 1537/7837 [01:05<04:12, 24.90it/s]


 20%|█▉        | 1541/7837 [01:06<03:49, 27.41it/s]


 20%|█▉        | 1545/7837 [01:06<04:47, 21.86it/s]


 20%|█▉        | 1548/7837 [01:06<06:32, 16.03it/s]


 20%|█▉        | 1551/7837 [01:06<06:19, 16.57it/s]


 20%|█▉        | 1556/7837 [01:06<04:50, 21.59it/s]


 20%|█▉        | 1561/7837 [01:07<03:54, 26.81it/s]


 20%|█▉        | 1565/7837 [01:07<03:31, 29.60it/s]


 20%|██        | 1569/7837 [01:07<03:26, 30.33it/s]


 20%|██        | 1574/7837 [01:07<03:01, 34.49it/s]


 20%|██        | 1578/7837 [01:07<02:56, 35.41it/s]


 20%|██        | 1582/7837 [01:07<02:54, 35.93it/s]


 20%|██        | 1587/7837 [01:07<02:41, 38.59it/s]


 20%|██        | 1592/7837 [01:07<03:10, 32.86it/s]


 20%|██        | 1596/7837 [

 26%|██▌       | 2012/7837 [01:28<03:15, 29.84it/s]


 26%|██▌       | 2016/7837 [01:28<03:01, 32.15it/s]


 26%|██▌       | 2020/7837 [01:28<03:26, 28.22it/s]


 26%|██▌       | 2024/7837 [01:28<03:43, 25.98it/s]


 26%|██▌       | 2027/7837 [01:28<03:37, 26.73it/s]


 26%|██▌       | 2030/7837 [01:29<04:00, 24.16it/s]


 26%|██▌       | 2033/7837 [01:29<04:21, 22.19it/s]


 26%|██▌       | 2036/7837 [01:29<06:26, 15.02it/s]


 26%|██▌       | 2038/7837 [01:29<08:34, 11.26it/s]


 26%|██▌       | 2042/7837 [01:30<06:18, 15.31it/s]


 26%|██▌       | 2046/7837 [01:30<05:01, 19.20it/s]


 26%|██▌       | 2051/7837 [01:30<04:03, 23.79it/s]


 26%|██▌       | 2056/7837 [01:30<03:53, 24.73it/s]


 26%|██▋       | 2061/7837 [01:30<03:24, 28.21it/s]


 26%|██▋       | 2066/7837 [01:30<03:17, 29.25it/s]


 26%|██▋       | 2070/7837 [01:30<03:09, 30.37it/s]


 26%|██▋       | 2074/7837 [01:31<03:22, 28.49it/s]


 27%|██▋       | 2079/7837 [01:31<02:58, 32.34it/s]


 27%|██▋       | 2083/7837 [

...

 80%|████████  | 6304/7837 [04:44<01:37, 15.78it/s]


 80%|████████  | 6306/7837 [04:44<01:33, 16.37it/s]


 81%|████████  | 6310/7837 [04:45<01:25, 17.82it/s]


 81%|████████  | 6315/7837 [04:45<01:04, 23.64it/s]


 81%|████████  | 6318/7837 [04:45<01:03, 24.01it/s]


 81%|████████  | 6322/7837 [04:45<00:57, 26.49it/s]


 81%|████████  | 6326/7837 [04:45<00:51, 29.13it/s]


 81%|████████  | 6330/7837 [04:45<00:55, 27.36it/s]


 81%|████████  | 6334/7837 [04:45<00:50, 29.59it/s]


 81%|████████  | 6338/7837 [04:45<00:50, 29.81it/s]


 81%|████████  | 6344/7837 [04:46<00:43, 34.15it/s]


 81%|████████  | 6348/7837 [04:46<00:42, 35.40it/s]


 81%|████████  | 6352/7837 [04:46<00:58, 25.27it/s]


 81%|████████  | 6357/7837 [04:46<00:53, 27.75it/s]


 81%|████████  | 6361/7837 [04:46<00:56, 26.23it/s]


 81%|████████  | 6367/7837 [04:46<00:46, 31.89it/s]


 81%|████████▏ | 6372/7837 [04:47<00:42, 34.48it/s]


 81%|████████▏ | 6377/7837 [04:47<00:40, 36.05it/s]


 81%|████████▏ | 6381/7837 [

 87%|████████▋ | 6830/7837 [05:04<00:51, 19.58it/s]


 87%|████████▋ | 6833/7837 [05:04<00:48, 20.60it/s]


 87%|████████▋ | 6836/7837 [05:04<01:02, 16.02it/s]


 87%|████████▋ | 6840/7837 [05:04<00:52, 19.05it/s]


 87%|████████▋ | 6843/7837 [05:05<00:51, 19.25it/s]


 87%|████████▋ | 6846/7837 [05:05<00:49, 19.99it/s]


 87%|████████▋ | 6849/7837 [05:05<00:45, 21.80it/s]


 87%|████████▋ | 6852/7837 [05:05<00:46, 21.09it/s]


 87%|████████▋ | 6856/7837 [05:05<00:38, 25.20it/s]


 88%|████████▊ | 6859/7837 [05:05<00:53, 18.15it/s]


 88%|████████▊ | 6862/7837 [05:06<00:53, 18.36it/s]


 88%|████████▊ | 6867/7837 [05:06<00:40, 23.86it/s]


 88%|████████▊ | 6870/7837 [05:06<00:48, 19.74it/s]


 88%|████████▊ | 6873/7837 [05:06<00:48, 19.87it/s]


 88%|████████▊ | 6876/7837 [05:06<00:45, 21.12it/s]


 88%|████████▊ | 6879/7837 [05:06<00:42, 22.48it/s]


 88%|████████▊ | 6883/7837 [05:06<00:38, 24.51it/s]


 88%|████████▊ | 6887/7837 [05:07<00:38, 24.55it/s]


 88%|████████▊ | 6890/7837 [

 93%|█████████▎| 7280/7837 [05:25<00:18, 30.94it/s]


 93%|█████████▎| 7284/7837 [05:26<00:16, 32.99it/s]


 93%|█████████▎| 7288/7837 [05:26<00:17, 31.67it/s]


 93%|█████████▎| 7292/7837 [05:26<00:16, 32.35it/s]


 93%|█████████▎| 7297/7837 [05:26<00:17, 31.22it/s]


 93%|█████████▎| 7301/7837 [05:26<00:20, 25.73it/s]


 93%|█████████▎| 7305/7837 [05:26<00:27, 19.42it/s]


 93%|█████████▎| 7309/7837 [05:27<00:23, 22.61it/s]


 93%|█████████▎| 7312/7837 [05:27<00:23, 22.13it/s]


 93%|█████████▎| 7315/7837 [05:27<00:23, 22.68it/s]


 93%|█████████▎| 7318/7837 [05:27<00:29, 17.74it/s]


 93%|█████████▎| 7322/7837 [05:27<00:25, 19.93it/s]


 93%|█████████▎| 7325/7837 [05:27<00:24, 21.07it/s]


 94%|█████████▎| 7328/7837 [05:28<00:22, 22.74it/s]


 94%|█████████▎| 7331/7837 [05:28<00:22, 22.67it/s]


 94%|█████████▎| 7335/7837 [05:28<00:33, 15.06it/s]


 94%|█████████▎| 7337/7837 [05:28<00:33, 14.80it/s]


 94%|█████████▎| 7341/7837 [05:28<00:26, 18.49it/s]


 94%|█████████▎| 7344/7837 [

 98%|█████████▊| 7704/7837 [05:49<00:06, 20.19it/s]


 98%|█████████▊| 7707/7837 [05:49<00:06, 21.20it/s]


 98%|█████████▊| 7710/7837 [05:49<00:07, 17.64it/s]


 98%|█████████▊| 7713/7837 [05:49<00:08, 15.35it/s]


 98%|█████████▊| 7715/7837 [05:49<00:07, 15.50it/s]


 98%|█████████▊| 7718/7837 [05:49<00:06, 18.30it/s]


 99%|█████████▊| 7721/7837 [05:49<00:05, 19.40it/s]


 99%|█████████▊| 7724/7837 [05:50<00:06, 18.36it/s]


 99%|█████████▊| 7728/7837 [05:50<00:04, 22.65it/s]


 99%|█████████▊| 7731/7837 [05:50<00:04, 24.33it/s]


 99%|█████████▊| 7734/7837 [05:50<00:04, 25.22it/s]


 99%|█████████▊| 7737/7837 [05:50<00:06, 15.54it/s]


 99%|█████████▉| 7740/7837 [05:51<00:06, 15.88it/s]


 99%|█████████▉| 7743/7837 [05:51<00:05, 18.12it/s]


 99%|█████████▉| 7746/7837 [05:51<00:04, 18.87it/s]


 99%|█████████▉| 7749/7837 [05:51<00:05, 17.56it/s]


 99%|█████████▉| 7754/7837 [05:51<00:03, 23.25it/s]


 99%|█████████▉| 7757/7837 [05:51<00:04, 19.40it/s]


 99%|█████████▉| 7760/7837 [

name  ratings  date  \
0                   미샤         4  2주 전   
1     Gyang gree young         5  3주 전   
2                  박진수         5  3달 전   
3              Sh Choi         5  7달 전   
6                  박은선         5  1년 전   
..                  ...      ...   ...   
921      young wu Kwon         5  1년 전   
922              강강수월래         4  1년 전   
924                원언니         5  1년 전   
925                김경영         4  1년 전   
928                김소연         5  1년 전   

                                               comment              search  \
0                    여기는 갈 때마다 새로운 느낌이 야 즐거운 시간이 되었습니다  장태산자연휴양림메타세콰이어산림욕장   
1                             하늘 보고 누워 힐링하기 너무 좋은 곳이에요  장태산자연휴양림메타세콰이어산림욕장   
2    잘 정리된 메타세쿼이아 숲에서 산림욕하기 좋은 곳으로 둘레길 걷기와 전망대까지 가벼...  장태산자연휴양림메타세콰이어산림욕장   
3                                        산책하기 너무 좋은 명소  장태산자연휴양림메타세콰이어산림욕장   
6                          주말 마자 애정 하는 장태산 나들이 단풍도 예뻐요  장태산자연휴양림메타세콰이어산림욕장   
..                                                 ...                 ...   
921                                               재밌어요                 오월드   
922                                      애들 놀고 구경거리는 굿                 오월드   
924                                초등생 전용 놀이로 아담하고 이뻐요                 오월드   
925                                               괜찮아요                 오월드   
928                                        겨울에도 놀기 좋아요                 오월드   

        keyword  
0    oworld_zoo  
1    oworld_zoo  
2    oworld_zoo  
3    oworld_zoo  
6    oworld_zoo  
..          ...  
921  oworld_zoo  
922  oworld_zoo  
924  oworld_zoo  
925  oworld_zoo  
928  oworld_zoo  

[7837 rows x 6 columns]

In [62]:
# set pandas option 
pd.set_option('display.max_rows', None) # 전체 행 보기
pd.set_option('display.max_columns', None) # 전체 열 보기 
pd.set_option('display.expand_frame_repr', False)

In [63]:
filtered_df

name  ratings    date                                            comment              search     keyword
0                                             미샤         4    2주 전                  여기는 갈 때마다 새로운 느낌이 야 즐거운 시간이 되었습니다  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
1                               Gyang gree young         5    3주 전                           하늘 보고 누워 힐링하기 너무 좋은 곳이에요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
2                                            박진수         5    3달 전  잘 정리된 메타세쿼이아 숲에서 산림욕하기 좋은 곳으로 둘레길 걷기와 전망대까지 가벼...  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
3                                        Sh Choi         5    7달 전                                      산책하기 너무 좋은 명소  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
6                                            박은선         5    1년 전                        주말 마자 애정 하는 장태산 나들이 단풍도 예뻐요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
7                                             아빠         5    1년 전                         무료인데다가 쉴 곳이 많고 시설이 잘 되어 있다  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
8                                         LEE가이버         5    1년 전  관람료 무료여서 좋고요 전망대까지 분 정도 걸리는 완만한 산책길은 대화하면서 올라가...  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
9                                            이해일         5    1년 전                                        대전의 좋은 산림욕장  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
10                                           이승주         5    1년 전                                       힐링 되고 아주 좋네요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
14                                           소병철         4    1년 전                                              힐링 코스  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
17                                           정기성         5    1년 전                                       주위기가 너무 새로워요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
19                                      Hs jeong         5    1년 전  메타세콰이 아이숲이 울창하고 좋네요 산책하기에도 좋고 담에는 맛있는 음식 가져와 돗...  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
22                                         보라빛냄새         5    1년 전                                                좋아요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
23                                           김기범         5    1년 전                                                좋아요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
1                                       Master K         5   9시간 전  장태산은 메타세쿼이아 나무가 높이높이 솟아 있어서 장관입니다 전망대나 흔들 다리도 ...            장태산자연휴양림  oworld_zoo
3                                           대전용달         5    2일 전                                              기 좋아요            장태산자연휴양림  oworld_zoo
4                                   Youngki Hong         5    2일 전                                                좋아요            장태산자연휴양림  oworld_zoo
7                                            정성식         5    4일 전       메타 크로스 나무가 너무 멋있고 기 좋고 푸르름에 건강해지는 느낌 진짜 좋았어요            장태산자연휴양림  oworld_zoo
9                                            정재곤         4    5일 전                                   다시 한가 보고 싶은 곳입니다            장태산자연휴양림  oworld_zoo
14                                           박은희         5    1주 전                                             정말 좋아요            장태산자연휴양림  oworld_zoo
19                                           장래소         3    1주 전           저 주일에 오랜만에 텐트를 펼치고 잠시나마 아이들과 휴식을 하고 왔습니다            장태산자연휴양림  oworld_zoo
23                                           이종후         5    1주 전                                   가볍게 산책하기 좋은 곳입니다            장태산자연휴양림  oworld_zoo
28                                    Kim Jinwoo         5    1주 전  쥐라기부터 단일 품종으로 생존하고 있는 메타세쿼이아 숲이 주연하는 초록의 향연을 맛...            장태산자연휴양림  oworld_zoo
31                                           황영주         5    2주 전                                             시힐링 최고            장태산자연휴양림  oworld_zoo
32                                        소크더라테스         5    2주 전                       기가 너무 좋아요 가족과 함께하는 시간을 즐겨보세요            장태산자연휴양림  oworld_zoo
33                                           이정민         5    2주 전                       메타세쿼이아의 이국적인 풍경과 피톤치드의 건강 힐링            장태산자연휴양림  oworld

In [64]:
filtered_path = os.path.join(os.getcwd(), 'filtered/google_review/')
filtered_path

'/home/aiffel-dj19/jungcheck/DataPreprocessing/filtered/google_review/'

In [65]:
keywords

{'장태산': 'jangtae_mountain',
 '계족산': 'gyejok_mountain',
 '동춘당': 'dongchundang',
 '으능정이문화의거리': 'uineungjeongi_street',
 '뿌리공원': 'ppuri_park',
 '엑스포': 'expo_science_park',
 '성심당': 'sungsimdang_bakery',
 '수통골': 'water_barrel',
 '유성온천': 'yuseong_hotspring',
 '한밭수목원': 'hanbat_arboretum',
 '국립중앙과학관': 'science_museum',
 '대청호': 'daecheong_lake',
 '대전문화예술단지': 'art_culture_complex',
 '시민천문대': 'observatory',
 '오월드': 'oworld_zoo'}

In [67]:
# keyword별로 dataframe 저장 
for _, keyword_en in keywords.items():
    result_df = filtered_df[filtered_df['keyword']==keyword_en] 
    save_path = filtered_path + f'{keyword_en}.csv'
    result_df.to_csv(save_path, header=True, index=False)

In [75]:
ls ./filtered/google_review/ # 파일 저장 경로내 파일 리스트 확인

art_culture_complex.csv   gyejok_mountain.csv   science_museum.csv
daecheong_lake.csv        hanbat_arboretum.csv  sungsimdang_bakery.csv
dongchundang.csv          jangtae_mountain.csv  uineungjeongi_street.csv
expo_science_park.csv     observatory.csv       water_barrel.csv
google_review_sample.csv  oworld_zoo.csv        yuseong_hotspring.csv
google_reviews.csv        ppuri_park.csv


In [69]:
# 마지막으로 저장한 csv 재확인
pd.read_csv(save_path)

name  ratings    date                                            comment              search     keyword
0                                              미샤         4    2주 전                  여기는 갈 때마다 새로운 느낌이 야 즐거운 시간이 되었습니다  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
1                                Gyang gree young         5    3주 전                           하늘 보고 누워 힐링하기 너무 좋은 곳이에요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
2                                             박진수         5    3달 전  잘 정리된 메타세쿼이아 숲에서 산림욕하기 좋은 곳으로 둘레길 걷기와 전망대까지 가벼...  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
3                                         Sh Choi         5    7달 전                                      산책하기 너무 좋은 명소  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
4                                             박은선         5    1년 전                        주말 마자 애정 하는 장태산 나들이 단풍도 예뻐요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
5                                              아빠         5    1년 전                         무료인데다가 쉴 곳이 많고 시설이 잘 되어 있다  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
6                                          LEE가이버         5    1년 전  관람료 무료여서 좋고요 전망대까지 분 정도 걸리는 완만한 산책길은 대화하면서 올라가...  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
7                                             이해일         5    1년 전                                        대전의 좋은 산림욕장  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
8                                             이승주         5    1년 전                                       힐링 되고 아주 좋네요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
9                                             소병철         4    1년 전                                              힐링 코스  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
10                                            정기성         5    1년 전                                       주위기가 너무 새로워요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
11                                       Hs jeong         5    1년 전  메타세콰이 아이숲이 울창하고 좋네요 산책하기에도 좋고 담에는 맛있는 음식 가져와 돗...  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
12                                          보라빛냄새         5    1년 전                                                좋아요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
13                                            김기범         5    1년 전                                                좋아요  장태산자연휴양림메타세콰이어산림욕장  oworld_zoo
14                                       Master K         5   9시간 전  장태산은 메타세쿼이아 나무가 높이높이 솟아 있어서 장관입니다 전망대나 흔들 다리도 ...            장태산자연휴양림  oworld_zoo
15                                           대전용달         5    2일 전                                              기 좋아요            장태산자연휴양림  oworld_zoo
16                                   Youngki Hong         5    2일 전                                                좋아요            장태산자연휴양림  oworld_zoo
17                                            정성식         5    4일 전       메타 크로스 나무가 너무 멋있고 기 좋고 푸르름에 건강해지는 느낌 진짜 좋았어요            장태산자연휴양림  oworld_zoo
18                                            정재곤         4    5일 전                                   다시 한가 보고 싶은 곳입니다            장태산자연휴양림  oworld_zoo
19                                            박은희         5    1주 전                                             정말 좋아요            장태산자연휴양림  oworld_zoo
20                                            장래소         3    1주 전           저 주일에 오랜만에 텐트를 펼치고 잠시나마 아이들과 휴식을 하고 왔습니다            장태산자연휴양림  oworld_zoo
21                                            이종후         5    1주 전                                   가볍게 산책하기 좋은 곳입니다            장태산자연휴양림  oworld_zoo
22                                     Kim Jinwoo         5    1주 전  쥐라기부터 단일 품종으로 생존하고 있는 메타세쿼이아 숲이 주연하는 초록의 향연을 맛...            장태산자연휴양림  oworld_zoo
23                                            황영주         5    2주 전                                             시힐링 최고            장태산자연휴양림  oworld_zoo
24                                         소크더라테스         5    2주 전                       기가 너무 좋아요 가족과 함께하는 시간을 즐겨보세요            장태산자연휴양림  oworld_zoo
25                                            이정민         5    2주 전                       메타세쿼이아의 이국적인 풍경과 피톤치드의 건강 힐링  

[효율적인 dataframe 사용](https://aldente0630.github.io/data-science/2018/08/05/a-beginners-guide-to-optimizing-pandas-code-for-speed.html)

In [70]:
# dataframe list comprehension과 apply 속도 비교 => 더 느렸음..?!

In [71]:
# test_df = copy.deepcopy(data_df)

In [72]:
# test_df['comment'] = test_df['comment'].apply(lambda row: spacingCorrect(row))

In [73]:
# test_df['comment'] = test_df['comment'].apply(lambda row: spellCorrect(row))